In [1]:
import pandas as pd
import numpy as np


chrom = 22
df = pd.read_pickle('chrom_%d_perm.pkl' % chrom)
df.set_index(['gene', 'intron'], inplace=True)
df.sort_index(inplace=True)
df.head()

chrom  lmm-pval       pos  qep-pval           snp_id
gene            intron                                                      
ENSG00000015475 6          22  0.115365  46907977  0.168976  snp_21_46907977
                6          22  0.322645  46908008  0.295156  snp_21_46908008
                6          22  0.097944  46908103  0.126963  snp_21_46908103
                6          22  0.957047  46908160  0.982791  snp_21_46908160
                6          22  0.957047  46908237  0.982791  snp_21_46908237

In [2]:
from bokeh.io import push_notebook, output_notebook
from bokeh.models import HoverTool, ColumnDataSource
from bokeh.plotting import figure, show, output_file
output_notebook()

import numpy as np
import colour
from scipy.special import betaincinv
from limix_plot import cycler_ as cycler
from collections import OrderedDict
from numpy import asarray as asa

def expected(n):
    lnpv = np.linspace(1/(n+1), n/(n+1), n, endpoint=True)
    return np.flipud(-np.log10(lnpv))

def xy(pv):
    
    return 

def rank_confidence_band(nranks):
    alpha = 0.01
    n = nranks
    k0 = np.arange(1, n+1)
    k1 = np.flipud(k0).copy()
    mean = k0 / (n + 1)
    return mean

def qqplot(method, color, df0, thr=1e-1, fill_alpha=0.2):

    p = figure(title = "%s :: chromossome %d" % (method.upper(), chrom),
               tools=['hover,zoom_in,zoom_out,box_zoom,save,pan,reset'], width=900)
    
    pv = df0['%s-pval' % method].values[:]
    lpv = -np.log10(pv)
    lpv_sort = np.argsort(lpv)
    expected_lpv = expected(len(lpv))

    ok = pv[lpv_sort] <= thr
    
    gene = asa([i[0] for i in df0.index.values[lpv_sort]])
    intron = asa([i[1] for i in df0.index.values[lpv_sort]])
    
    source = ColumnDataSource(data=dict(
        xname=expected_lpv[ok],
        yname=lpv[lpv_sort][ok],
        gene=gene[ok],
        intron=intron[ok],
        snp_id=df0['snp_id'][lpv_sort][ok],
        pval=pv[lpv_sort][ok],
        pos=df0['pos'][lpv_sort][ok]
    ))
    
    p.circle('xname', 'yname', source=source, color=color,
             fill_alpha=fill_alpha, line_width=0, line_color=None)
    
    p.select_one(HoverTool).tooltips = [
        ('gene', '@gene'),
        ('intron', '@intron'),
        ('snp_id', '@snp_id'),
        ('pos', '@pos'),
        ('p-value', '@pval'),
    ]
    mean = rank_confidence_band(len(lpv))
    me = [-np.log10(m) for m in mean]
    p.line([me[0], me[-1]], [me[0], me[-1]], color='black')
    show(p)

Loading BokehJS ...

In [3]:
qqplot('qep', 'red', df)

In [4]:
df.head()

chrom  lmm-pval       pos  qep-pval           snp_id
gene            intron                                                      
ENSG00000015475 6          22  0.115365  46907977  0.168976  snp_21_46907977
                6          22  0.322645  46908008  0.295156  snp_21_46908008
                6          22  0.097944  46908103  0.126963  snp_21_46908103
                6          22  0.957047  46908160  0.982791  snp_21_46908160
                6          22  0.957047  46908237  0.982791  snp_21_46908237

In [5]:
pvals = df['qep-pval'][:]

# Get the gene-intron pair having the SNP with lowest p-value

In [6]:
gene = df.loc[pvals.argmin()]
gene = gene.reset_index()
gene_name, intron = gene['gene'][0], gene['intron'][0]
gene = gene.set_index('snp_id')

## Here is the SNP ID

In [7]:
gene['qep-pval'].argmin()

'snp_21_43667865'

# Look how low is the p-value

In [8]:
qqplot('qep', 'red', gene.reset_index().set_index(['gene', 'intron']), 1.0, 1.0)

In [9]:
gene.head()

gene  intron  chrom  lmm-pval       pos  \
snp_id                                                                     
snp_21_43664791       ENSG00000243811       5     22  0.349167  43664791   
snp_21_43664993       ENSG00000243811       5     22  0.027642  43664993   
snp_21_43665024       ENSG00000243811       5     22  0.715747  43665024   
snp_21_43665240       ENSG00000243811       5     22  0.177403  43665240   
indel:1D_21_43665304  ENSG00000243811       5     22  0.994227  43665304   

                          qep-pval  
snp_id                              
snp_21_43664791       9.108213e-09  
snp_21_43664993       4.187111e-03  
snp_21_43665024       7.886740e-05  
snp_21_43665240       7.843184e-03  
indel:1D_21_43665304  2.337135e-03

In [10]:
from horta_exp.introns.tasks.qtl import _randomly_associated_gene_intron
from horta_exp.introns.tasks.qtl import _get_genotype_data

In [11]:
(a_gene_name, a_intron, a_cid) = _randomly_associated_gene_intron(gene_name, intron, chrom)

In [12]:
print(a_gene_name, a_intron, a_cid)

ENSG00000160179 21 21


In [13]:
a_K, a_G, a_pos, a_fam, a_snp_ids = _get_genotype_data(a_gene_name, a_intron, a_cid)

In [14]:
a_G.shape

(465, 570)

# I will look into the trait itself now

In [15]:
import six
try:
    import cPickle as pkl
except ImportError:
    import pickle as pkl
import blosc
from os.path import join

_root = '/hps/nobackup/stegle/users/lab/dataset/'
_folder_traits = join(_root, 'alternative-splicing',
                      'quant_splicing',
                      'transcript-qtls')

_folder_genotype = join(_root, '1000G', 'plink', 'horta')

def get_intron_events():
    with open(join(_folder_traits, 'intron_events_filter3.pkl.blp'), 'rb') as f:
        msg = blosc.decompress(f.read())
        if six.PY3:
            return pkl.loads(msg, encoding='latin-1')
        else:
            return pkl.loads(msg)

In [16]:
ie = get_intron_events()

In [17]:
traits = ie.loc[(gene_name, intron)]

In [18]:
traits.head()

assay  nsuc  ntri
gene            intron                                  
ENSG00000243811 5       HG00096.1.M_111124_6   225   311
                5       HG00097.7.M_120219_2   396   646
                5       HG00099.1.M_120209_6    63   162
                5       HG00099.5.M_120131_3    75   184
                5       HG00100.2.M_111215_8   113   277

# Lets see if the number of trials is crazy

In [19]:
import numpy as np

p = figure(title = "(%s, %d)" % (gene_name, intron),
           tools=['save,reset'], width=900)

hist, edges = np.histogram(traits['ntri'], density=True, bins=50)
p.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:],
       fill_color="#036564", line_color="#033649")
p.xaxis.axis_label = '# of trials'
show(p)

In [20]:
gene.head()

gene  intron  chrom  lmm-pval       pos  \
snp_id                                                                     
snp_21_43664791       ENSG00000243811       5     22  0.349167  43664791   
snp_21_43664993       ENSG00000243811       5     22  0.027642  43664993   
snp_21_43665024       ENSG00000243811       5     22  0.715747  43665024   
snp_21_43665240       ENSG00000243811       5     22  0.177403  43665240   
indel:1D_21_43665304  ENSG00000243811       5     22  0.994227  43665304   

                          qep-pval  
snp_id                              
snp_21_43664791       9.108213e-09  
snp_21_43664993       4.187111e-03  
snp_21_43665024       7.886740e-05  
snp_21_43665240       7.843184e-03  
indel:1D_21_43665304  2.337135e-03

# Now number of trials versus number of successes

In [21]:
p = figure(title = "(%s, %d)" % (gene_name, intron),
           tools=['save,reset'], width=900)

p.circle(traits['ntri'], traits['nsuc'])
p.xaxis.axis_label = '# of trials'
p.yaxis.axis_label = '# of successes'
show(p)

Conclusion so far is that the trait is all fine, so it might have to do with genotype.
MAF, maybe? I will have a look at it now.

In [22]:
from lim.tool.normalize import stdnorm
from lim.genetics.qtl import scan
from lim.genetics.phenotype import (NormalPhenotype,
                                    BinomialPhenotype)

In [23]:
from horta_exp.introns.tasks.qtl import _get_trait


iid, nsuc, ntri = _get_trait(gene_name, intron)

In [24]:
idx = []
for iid_ in iid:
    q = "iid == '%s'" % iid_
    idx.append(a_fam.query(q)['i'].values[0])

In [25]:
pheno = BinomialPhenotype(np.asarray(nsuc), np.asarray(ntri))
_a_G = a_G[idx,:]
_a_K = a_K[idx,:][:,idx]
_a_G = np.asarray(_a_G)
_a_K = np.asarray(_a_K)
covariates = np.ones((_a_K.shape[0], 1))

In [26]:
s = scan(pheno, _a_G, K=_a_K, covariates=covariates, progress=False)

0it [00:00, ?it/s]

[ 1.          0.43165273]


1it [00:11, 11.53s/it]

[ 1.00004083  0.43165236]


2it [00:19, 10.54s/it]Maximum number of EP iterations has been attained.


...

41it [06:20,  8.75s/it]

[ 1.00006075  0.43165218]


42it [06:29,  9.00s/it]

[ 1.00006075  0.43165218]


KeyboardInterrupt: 

In [27]:
s.pvalues()

array([  1.21000838e-73,   1.72304794e-73,   6.31644511e-74,
         7.28769533e-74,   1.42868240e-73,   1.42868240e-73,
         1.72148098e-73,   1.75613407e-73,   1.23092024e-73,
         3.29702342e-74,   1.45930400e-74,   3.29702342e-74,
         1.62329525e-73,   1.85178761e-73,   6.31644511e-74,
         1.74673496e-73,   1.65960106e-73,   1.88524346e-73,
         6.04737214e-74,   1.95812980e-73,   1.75613407e-73,
         1.23092024e-73,   1.65960106e-73,   1.28171657e-73,
         4.57376776e-74,   1.95812980e-73,   1.92259451e-73,
         1.74673496e-73,   1.74673496e-73,   1.74673496e-73,
         6.31644511e-74,   6.31644511e-74,   1.48056893e-73,
         1.65832465e-73,   4.84296443e-74,   2.14186526e-74,
         4.84296443e-74,   1.61054748e-73,   7.32757752e-74,
         1.91364087e-73,   7.22158469e-74,   1.90742970e-73,
         6.26337401e-74,   1.96566478e-73,   8.66656801e-74,
         1.71706197e-73,   5.35304785e-74,   7.01278154e-74,
         9.83721655e-74,

In [27]:
np.savez('/homes/horta/workspace/debug.npz', nsuc=np.asarray(nsuc), ntri=np.asarray(ntri), G=_a_G, K=_a_K, covariates=covariates)

In [ ]:
s.null_lml()

In [ ]:
s.alt_lmls()

In [ ]:
s._fixed_ep.compute(covariates, np.random.randn(covariates.shape[0], 1))

In [ ]:
s._fixed_ep.compute(covariates, np.zeros((covariates.shape[0], 1)))

# Genotype

In [ ]:
from horta_exp.introns.fetch_data import get_intron_events, get_chromossome, get_kinship
from horta_exp.introns.fetch_data import get_positions

In [ ]:
cid = 22
pos = get_positions()
pos = pos.query("(gene == '%s') & (intron == %d)" % (gene_name, intron))
start_pos, end_pos = pos['start_pos'].values[0], pos['end_pos'].values[0]

df = get_intron_events()
df = df.loc[(gene_name, intron)]
df['iid'] = df['assay'].apply(lambda x: x.split('_')[0].split('.')[0])

K = get_kinship()
ws = 50000

(bim, fam, G) = get_chromossome(cid)

random = np.random.RandomState(0)
G = G[:, random.permutation(range(G.shape[1]))]

window_start = start_pos-ws
window_end = end_pos+ws
query = "(chrom == '%d') & (pos >= %d) & (pos <= %d)" % (cid, window_start, window_end)
bim = bim.query(query).sort_index(level=[1])

snp_idx = bim['i'].values
snp_ids = bim['snp'].values
pos = [v[1] for v in bim.index.values]

G = G[:,snp_idx]

data = dict(ntri=[], nsuc=[], idx=[], snp_id=snp_ids)

for r in df.iterrows():
    data['nsuc'].append(r[1][1])
    data['ntri'].append(r[1][2])
    q = "iid == '%s'" % r[1][3]
    data['idx'].append(fam.query(q)['i'].values[0])

G = G[data['idx'],:]
K = K[data['idx'],:][:,data['idx']]

In [ ]:
snp_id = gene['qep-pval'].argmin()
print(snp_id)

In [ ]:
idx = np.where(snp_ids == snp_id)[0][0]
snp_genotype = G[:, idx]

In [ ]:
snp_genotype

In [ ]:
from numpy import asarray, minimum

def _maf(X):
    r"""Compute minor allele frequencies.
    It assumes that `X` encodes 0, 1, and 2 representing the number
    of alleles.
    Args:
        X (array_like): Genotype matrix.
    Returns:
        array_like: minor allele frequencies.
    """
    X = asarray(X, float)
    s0 = X.sum(0)
    s0 /= float(2*X.shape[0])
    s1 = 1 - s0
    return minimum(s0, s1)

In [ ]:
maf = _maf(snp_genotype[:, np.newaxis])[0]

In [ ]:
print('%s MAF: %.5f' % (snp_id, maf))

In [ ]:
from lim.tool.normalize import stdnorm
from lim.genetics.qtl import scan
from lim.genetics.phenotype import (NormalPhenotype,
                                    BinomialPhenotype)

In [ ]:
pheno = BinomialPhenotype(traits['nsuc'], traits['ntri'])
covariates = np.ones((K.shape[0], 1))
s = scan(pheno, G, K=K, covariates=covariates, progress=False)

In [ ]:
print(s.pvalues().min())
print(np.argmin(s.pvalues()))
print(snp_ids[np.argmin(s.pvalues())])

In [ ]:
print(G[:,np.argmin(s.pvalues())])

QEP really thinks that SNP is associated with the trait.

In [ ]:
y = np.asarray(traits['nsuc'], float)/traits['ntri']
np.corrcoef(snp_genotype, y)

In [ ]:
corrs = []
for i in range(G.shape[1]):
    corrs += [np.corrcoef(y, G[:,i])[0,1]]

In [ ]:
from bokeh.models import Jitter
p = figure(title = "Pearson correlation trait versus genotypes",
           tools=['save,reset'], width=400)

p.circle(x={'value': 1, 'transform': Jitter(width=0.4)}, y=corrs,
         color="navy", alpha=0.3)

show(p)

In [ ]:
(o_bim, o_fam, o_G) = get_chromossome(cid)

o_random = np.random.RandomState(0)
original_perm = o_random.permutation(range(o_G.shape[1]))

acc = o_bim.reset_index().set_index('snp').sort_index()
print(acc.loc[(snp_id,)]['i'])
o_idx = original_perm[acc.loc[(snp_id,)]['i']]

In [ ]:
snp_id_actually_used = o_bim[o_bim['i'] == o_idx]['snp'][0]

In [ ]:
snp_id_actually_used

In [ ]:
df0 = o_bim[o_bim['snp'] == snp_id_actually_used]

In [ ]:
df0.reset_index()['pos'][0]

In [ ]:
pos = get_positions()
pos = pos.query("(gene == '%s') & (intron == %d)" % (gene_name, intron))
start_pos, end_pos = pos['start_pos'].values[0], pos['end_pos'].values[0]

In [ ]:
start_pos, end_pos